# Diversity sub-model for *Inconsistent belief aggregation in diverse and polarised groups*

In [ ]:
# Install packages used in this notebook
%pip install taupy numpy pandas statsmodels seaborn matplotlib ptitprince networkx

## Packages

In [ ]:
# theory of dialectical structures
from taupy import *

# system tools
import random
from concurrent.futures import ProcessPoolExecutor

# data analysis & storage
import numpy as np
import pandas as pd
import statsmodels.formula.api as smf

# visuals
import seaborn as sea
import matplotlib.pyplot as plt
import ptitprince as pt
import networkx as nx

## Helper functions to generate diverse samples

In [ ]:
def normal_distribution(scale, x):
    """
    Basic normal distribution function
    """
    return (np.pi*scale) * np.exp(-0.5*((x)/scale)**2)

def return_normal_values(scale, values):
    """
    Obtain a list of points on the normal distribution
    """
    return [normal_distribution(scale, i) for i in values]

def Gini_Simpson_from_distribution(distribution):
    """
    Calculate the Gini–Simpson index based on a distribution. The items of the input
    iterable `distribution` should indicator type expression of the respective item.
    An example input would be `[1, 1, 2, 5, 4, 4, 2, 3]` for a population with two 
    individuals belonging to the first type, two for the second, etc.
    """
    population_size = len(distribution)
    items = set(distribution)
    proportions = [len([p for p in distribution if p == i]) for i in items]
    return  1 - sum([(c/population_size)**2 for c in proportions])

## Functions to conduct experiments

In [ ]:
def multiprocess_diversity_experiment(
    n=1,
    *,
    max_workers=None,
    settings={}
):
    """
    A function to spawn multiple experiment processes. Control the 
    maximum number of used CPUs through `max_workers`, and `n` is the
    number of experiments. `settings` are passed on to the individual
    `diversity_experiment()`s.
    """
    with ProcessPoolExecutor(max_workers=max_workers) as executor:
        sim_results = [executor.submit(
            diversity_experiment,
            **settings
        ) for _ in range(n)]

    return pd.concat(
        [i.result() for i in sim_results],
        ignore_index=True
        )

In [ ]:
def diversity_experiment(*,
    density_factor = 5, 
    distribution_factor = 10,
    densities = [0.4, 0.5, 0.6, 0.7, 0.8],
    distributions = [
        0.15, 0.3, 0.45, 0.475, 0.5, 0.55, 0.65, 0.75, 0.85, 1, 1.25, 1.5, 1.75, 
        2, 3, 4, 5, 6],
    population_size = 51
    ):
    """
    Perform a single diversity experiment. The number of argument maps created for 
    each point of inferential density in `densities` is given by `density_factor`. 
    
    The number of agents is controlled by `population_size` – an odd number is 
    recommended, or otherwise `aggregated_position_of_winners()` will eventually
    raise errors in case of a tie.
    
    The `distributions` are scaling factors passed to the helper functions defined 
    above. They control from which types, or clusters, agents are drawn. For example, 
    with a distribution scaled by the factor 0.15, agents are mostly drawn from only 
    one cluster, but each cluster is about equally likely to be drawn for a distribution 
    scaled by the factor 6. The `distribution_factor` controls how many samples are drawn
    per distribution point. The total number of samples from a single experiment is thus
    given by multiplying 
    
    ```
    density_factor * len(densities) * distribution_factor * len(distributions)
    ```
    """

    results = []

    for d in densities:
        for _ in range(density_factor):
            pops = []
            while not pops:
                # Try to generate a population from an argument map, by 
                # first synthetising an argument map.
                m = generate_hierarchical_argument_map(max_density=d)
                s = satisfiability(m, all_models=True)
                diffmatrix = clustering_matrix(
                    s, measure=normalised_hamming_distance,
                    scale=-2
                    )
                # ... and then clustering the population of admissible agent
                # belief systems with Affinity Propagataion.
                #
                # Affinity Propagation does not always converge. In this case, a 
                # Warning is issued, and `pops` is not populated. The process then
                # restarts by generating a new argument map.
                pops = [[s[i] for i in j] for j in affinity_propagation(s, clustering_settings={"scale": -2})]
                # Shuffle the list of clusters to avoid any potential return
                # pattern of Affinity Propagation
                random.shuffle(pops)

            for g in distributions:
                for _ in range(distribution_factor):
                    # Randomly choose clusters, weighted
                    # by the scales in the iterable `distributions`.
                    rnd_chs = random.choices(
                        list(range(len(pops))), 
                        weights=return_normal_values(g, list(range(len(pops)))),
                        k=population_size
                        )
                    
                    # Obtain the Gini–Simpson value of the cluster sample.
                    try:
                        G_S = Gini_Simpson_from_distribution(rnd_chs)
                    except ZeroDivisionError:
                        G_S = 0

                    # Store the number of clusters
                    num_groups = len(set(rnd_chs))

                    # Randomly draw agents beloning to each of the selected clusters
                    sel_pos = [random.choice(pops[c]) for c in rnd_chs]

                    # Cast a sentence-wise majority vote among the selected agents
                    rt_pos = Position(
                        m,
                        aggregated_position_of_winners(sel_pos)
                    )

                    # Check whether the aggregated opinion is consistent or not
                    # (will store True or False)
                    consistency = rt_pos.is_coherent()

                    # More diagnostic values. First, the number of unique positions held
                    # in the drawn sample
                    number_of_unique_positions = len([
                    dict(i) for i in set(frozenset(position.items())
                                            for position in sel_pos)
                    ])
                    
                    # The number of agents who's belief system exactly matches the aggregated
                    # opinion.
                    majority_holders = len([p for p in sel_pos if p==rt_pos])/len(sel_pos)

                    # The mean distance between agents and the majority opinion.
                    mean_distance = pd.Series([
                        hamming_distance(p, rt_pos) for p in sel_pos
                    ]).mean()
                    
                    # ... and the variance of that distance.
                    distance_var = pd.Series([
                        hamming_distance(p, rt_pos) for p in sel_pos
                    ]).var()

                    # Store all of the results, and continue the iteration (start anew from 
                    # the top).
                    results.append((d, m, g, G_S, num_groups, consistency, 
                                    majority_holders, mean_distance, distance_var,
                                    sel_pos, number_of_unique_positions))
    
    # Pandas data managemnt
    return pd.DataFrame(
        results,
        columns=["inferential density", "debate", "g", "Gini–Simpson", 
                "number of groups", "consistency", 
                "holders of majority position", "mean distance to majority", 
                "distance variation", "population", "unique positions"]
        )


# Single model run

Here we call a single model run with two argument maps per density point, and two density points.

In [ ]:
data_single_run = diversity_experiment(
    density_factor = 2, 
    distribution_factor = 1,
    densities = [0.5, 0.8],
    )

In [ ]:
g = sea.FacetGrid(data_single_run, col="inferential density", aspect=4/5)
g.map(sea.swarmplot, "consistency", "Gini–Simpson", size=6, dodge=True, color="k", order=None)
plt.savefig("SingleModelRun-Diversity.png",bbox_inches="tight",dpi=300)

# Multiple model runs

Info: As described in the code above, Affinity Propagation is not always able to cluster the valid opinions on an argument map. In this case, the argument map is discarded and a new one is generated automatically. A Warning “Affinity propagation did not converge, this model will not have any cluster centers” will appear in the output. This is not a concern, as a new argument map is simply generated.

In [ ]:
df1 = multiprocess_diversity_experiment(
    n=20,
    settings={
        "densities": [0.4, 0.5, 0.6, 0.7, 0.8],
        "density_factor": 2,
        "distribution_factor": 3
    }
)

In [ ]:
sea.set_style("ticks",{'axes.grid' : True}) # Produce horizontal grid guidelines
f, ax = plt.subplots(figsize=(12, 5))
ax=pt.RainCloud(hue = "consistency", y = "Gini–Simpson", x = "inferential density", data = df1,
                width_viol = .5, ax = ax, alpha = .5, dodge = True,
                palette=sea.color_palette(n_colors=2), cut=0,
                scale="count"
)

# The standard legend positioning by RainCloud() is not optimal, we adjust it here.
handles, labels = ax.get_legend_handles_labels() # Get legend entries
ax.get_legend().remove() # Removes the old legend
plt.legend(handles[0:2], # Creates a new legend
           #labels[0:len(labels)//2], # Default “False” and “True” consistency labels
           ["Inconsistent", "Consistent"], #Custom labels instead of “True” and “False”
           bbox_to_anchor=(.5, 1), loc=8,
           title = "Consistency of majority opinion", ncol=2)
# RainCloud() is not compatible to seaborn 0.12 and above. With seaborn 0.12, the legend could
# be moved more easily:
# ax.legend([False, True], bbox_to_anchor=(.5, 1), ncol=3, title="Consistency", frameon=False)
# Saves the Plot
plt.savefig("Experiment-Diversity.png",bbox_inches="tight",dpi=300)

# Statistical analysis

For easier interpretation of the “unit of change” parameter in the Logit model, we normalise the Gini–Simpson values.

In [ ]:
df1["normGS"] = df1["Gini–Simpson"]*100
df1["consistencyNum"] = df1["consistency"].astype(int)

In [ ]:
logit_model = smf.logit("consistencyNum ~ normGS", data=df1).fit()
logit_model.summary()

We measure Cohen's $f^2$: $$f^2=\frac{R^2}{1-R^2}$$

In [ ]:
logit_model.prsquared / (1-logit_model.prsquared)

Obtain the $\chi^2$ value and $p$ to check the models significance.

In [ ]:
{"Chisq": logit_model.llr, "p": logit_model.llr_pvalue}

# Summary data table

In [ ]:
df2 = df1[["Gini–Simpson", "consistency"]].copy()

In [ ]:
df2["interval"] = pd.cut(df2["Gini–Simpson"], bins=[0, 0.25, 0.5, 0.75, 1], include_lowest=True)

In [ ]:
df2.groupby(["interval"]).mean()["consistency"]